In [28]:
import json

import pandas as pd

from fbprophet import Prophet
from fbprophet.plot import plot_plotly, plot_components_plotly, plot_yearly
from fbprophet.diagnostics import cross_validation

import plotly.express as px
import plotly.io as pio

import warnings
warnings.filterwarnings('ignore')

## Data Scope
- Duration from ```2017-01-01``` to ```2022-03-01```
- Searching 4 keywords ["#นัดเย็ดกทม", "#onsกทม", "#fwbกทม", "#นัดเย็ดกรุงเทพ"]

### All User Data

In [2]:
df_user = pd.read_csv("data/total_user_data_20170101_20220301.csv") 
df_user.drop(columns = "Unnamed: 0", inplace = True)

In [3]:
# Drop duplication on 'id'
df_user.drop_duplicates(subset = "id", inplace = True)
df_user['created_at_date_thtz'] = pd.to_datetime(df_user['created_at_date_thtz'])
df_user['created_year_month'] = df_user['created_at_date_thtz'].dt.strftime('%Y-%m')

df_user = df_user[df_user['created_year_month'] != '2022-03']
df_user.reset_index(drop = True, inplace = True)

In [4]:
num_by_day = df_user.groupby("created_at_date_thtz").agg({"id":"count"}).reset_index()
px.line(num_by_day, x = "created_at_date_thtz", y ="id",
        title = "Number of created account : Daily All keywords",
        width = 900, height= 400)

In [5]:
num_by_yearmonth = df_user.groupby("created_year_month").agg({"id":"count"}).reset_index()
px.line(num_by_yearmonth, x = "created_year_month", y ="id",
        title = "Number of created account : Monthly All keywords",
        width = 900, height= 400)

## Tweet Data

In [6]:
df_tweet = pd.read_csv("data/total_tweet_data_20170101_20220301.csv")

In [7]:
'''
Data Cleaning
- Drop un-related column
- Drop duplicate Tweet id
- Convert created date to "Year-Month" for aggregation
'''

df_tweet.drop(columns = ["Unnamed: 0"], inplace = True)
df_tweet.drop_duplicates(subset = "id", inplace = True)
df_tweet['created_at_date_thtz'] = pd.to_datetime(df_tweet['created_at_date_thtz'])
df_tweet['created_year_month'] = df_tweet['created_at_date_thtz'].dt.strftime('%Y-%m')


# Drop latest montn out due to incomplete data
df_tweet = df_tweet[df_tweet['created_year_month'] != '2022-03']
df_tweet.reset_index(drop= True, inplace = True)

### Overall Number of Tweet

In [8]:
num_by_monthly = df_tweet.groupby(["created_year_month"]).agg({"id":"count"}).reset_index()
num_by_monthly.rename(columns = {"id" : "Number of Tweet",  
                                   "created_year_month" : "Tweet Date"}, inplace = True)

pio.templates.default = "simple_white"
px.line(num_by_monthly, x = "Tweet Date", y ="Number of Tweet",
        title = "Number of Tweet : Monthly Total",
        width = 900, height= 500)

In [9]:
num_by_keymonthly = df_tweet.groupby(["created_year_month", "keywords"]).agg({"id":"count"}).reset_index()
num_by_keymonthly.rename(columns = {"id" : "Number of Tweet",  
                                   "keywords" : "#hashtag",
                                   "created_year_month" : "Tweet Date"}, inplace = True)

pio.templates.default = "simple_white"
num_by_keymonthly_line = px.line(num_by_keymonthly, x = "Tweet Date", y ="Number of Tweet", color = "#hashtag",
                                title = "Number of Tweet : Monthly by keywords",
                                width = 900, height= 500)
num_by_keymonthly_line
#num_by_keymonthly_line.write_html("Number of Tweet - Monthly Keywords.html")

### Tweet Frequency

In [15]:
tweetnum_user_monthly = df_tweet.groupby(['author_id', "created_year_month"]).agg({"id" : "count"}).reset_index()
tweetnum_user_monthly.rename(columns = {"author_id" : "Account", 
                                        "id" : "Number of Tweet", 
                                        "created_year_month" : "Tweet Date"}, inplace = True)                    

In [19]:
px.histogram(tweetnum_user_monthly[tweetnum_user_monthly['Number of Tweet'] < 50], 
            x = "Number of Tweet", title = "Count of Tweet Number Monthly Frequency/User : < 50 Tweet Month",
            width = 700, height= 500)

In [20]:
px.histogram(tweetnum_user_monthly[tweetnum_user_monthly['Number of Tweet'] >= 50], 
            x = "Number of Tweet", title = "Count of Tweet Number Monthly Frequency/User : > 50 Tweet Month",
            width = 700, height= 500)

### Trend and Seasoanlity

### Location Analysis

In [36]:
df_geononna = df_tweet[~df_tweet['geo'].isna()]
df_geona = df_tweet[df_tweet['geo'].isna()]

In [37]:
df_geononna['geo_dict'] = df_geononna['geo'].apply(lambda x: json.loads(x.replace("'", "\"")))
df_geononna['place_id'] = df_geononna['geo_dict'].apply(lambda x:  x['place_id'] if 'place_id' in x else None)
df_geononna['coordinates'] = df_geononna['geo_dict'].apply(lambda x:  x['coordinates']['coordinates'] if 'coordinates' in x else None)

In [38]:


for text_body in df_tweet['text']:
    if "จุฬา" in text_body:
        print(text_body)
        print("----")
        print("")

RT @miraixxx51: แค่อยากลองเล่นกล้องบ้างง🐰#fwbกทม #จุฬา #มธ #อัสสัมชัญ #เกษตรบางเขน #เรียลมัธยม #เรียลมหาลัย https://t.co/FH5uK8G9Re
----

RT @miraixxx51: มีใครชอบปากนุ่มๆเค้ามุ้ยยDM🙈🤍#เรียลชาย  #fwbกทม #fwbรังสิต #พลัมบียู #จุฬา #มธ #อัสสัมชัญ  #เรียลมัธยม #เรียลมหาลัย #BU #ธร…
----

RT @miraixxx51: มีใครชอบปากนุ่มๆเค้ามุ้ยยDM🙈🤍#เรียลชาย  #fwbกทม #fwbรังสิต #พลัมบียู #จุฬา #มธ #อัสสัมชัญ  #เรียลมัธยม #เรียลมหาลัย #BU #ธร…
----

เงี่ยนมากๆ 🥺 หาคนเน้ดดด แถวจุฬา #fwbกทม #นัดเย็ดจุฬา #นัดเย็ดกรุงเทพ  #นัดเย็ด
----

RT @miraixxx51: ใครอยากมาจับผีเสื้อห้องมี้บ้างDM🙈🤍#เรียลชาย  #fwbกทม #นัดเย็ดกทม #bu #fwbรังสิต #นัดเย็ดรังสิต #พลัมบียู #จุฬา #มธ #อัสสัม…
----

RT @k18078888: เหงาๆ  มาคุยกันนะคะคุณรร🥺 
#นัดเย็ดกรุงเทพ #นัดเย็ดกทม #นัดเย็ดจุฬา #นัดเย็ดรังสิต #นัดเย็ดมช #นัดเย็ดมอกรุง #fwbกทม #เรียลห…
----

เงี่ยนจังงือ ตื่นมาก็เงี่ยน มานัดกันงับ อยากกินเด็กๆมัธยมมหาลัยมีมั้ยย #นัดเย็ดกทม #นัดเย็ดกรุงเทพ #สาวอวบอ้วน #สาวอวบ #เงี่ยนอยากโดนเย็ด #ONSกรุงเทพ #fwbกทม #เรียลมัธยม #เรียลนักศึกษา #นัดเ